In [44]:
"""
things to add
1) takes imgs - done                   2) augment imgs - done                      3) get coordinates of hand out of the imgs and store it in a df - done
4) train & test the model - done       5) simulate hand gesture on a drone -  done         6) voice recognition - somewhat done

7) fix discrepencies in data input and gestures   - done       8) use multiple hands(give data for multiple hand) 
9) add a bit more varibility in data so it recognises hand better              10) adding a feature to tell which coordinates to move to using voice        
                     
11) recognise even if we do back hand(add data)                       12) if not in the set of gesture doesnt give an output of invalid

add more org data, one v all, whisper, training different data for opposite hand(the img would be flipped)
"""

'\nthings to add\n1) takes imgs - done                   2) augment imgs - done                      3) get coordinates of hand out of the imgs and store it in a df - done\n4) train & test the model - done       5) simulate hand gesture on a drone -  done         6) voice recognition - somewhat done\n\n7) fix discrepencies in data input and gestures   - done       8) use multiple hands(give data for multiple hand) \n9) add a bit more varibility in data so it recognises hand better              10) adding a feature to tell which coordinates to move to using voice        \n                     \n11) recognise even if we do back hand(add data)                       12) if not in the set of gesture doesnt give an output of invalid\n\nadd more org data, one v all, whisper, training different data for opposite hand(the img would be flipped)\n'

# 1) hand detection

In [4]:
# 1) importing libraries
import pandas as pd
import numpy as np
import time

import os
import cv2

from mediapipe import tasks, Image, solutions,ImageFormat
from mediapipe.framework.formats import landmark_pb2

from tensorflow.keras.preprocessing.image import ImageDataGenerator
gesture_list = ['back', 'down', 'flip', 'front', 'left', 'right', 'up']# add hover

In [46]:
# 2) taking pictures and then augmenting data 

def augment_images(input_dir, output_dir, augment_count=250):  
    data_gen = ImageDataGenerator(rotation_range = 30, width_shift_range = 0.4, height_shift_range = 0.4, shear_range = 0.2, zoom_range = 0.2, brightness_range = [0.8, 1.4], fill_mode = 'nearest')

    for label in os.listdir(input_dir):
        label_path =  os.path.join(input_dir, label)
        save_path = os.path.join(output_dir, label)
        os.makedirs(save_path, exist_ok=True)  

        for img_file in os.listdir(label_path):
            img_path = os.path.join(label_path, img_file)

            img  = cv2.imread(img_path)    
            img = cv2.resize(img, (128,128))
            img = img[np.newaxis, ...]   

            for i,  augmented_img in enumerate (data_gen.flow(img, batch_size=1) ):  
               
                cv2.imwrite(os.path.join(save_path,   f"{img_file.split('.')[0]}_aug_{i}.jpg"), augmented_img[0].astype(np.uint8)) 
                if i > augment_count:
                    break

# augment_images('dataset/org', 'dataset/augmented')

In [47]:
# 3) converting images to coordinates

def get_coords(img):
    base_op = tasks.BaseOptions  # setting up the model
    vis_mode = tasks.vision.RunningMode.IMAGE    # specifeis img detection as opposed to video or anything else
    landmaker = tasks.vision.HandLandmarker   # find the position of the hand
    landmarker_op = tasks.vision.HandLandmarkerOptions   # has op to config hand detection
    
    # uses pre trained model(), 
    # .task is a model format used by tf Task API, which makes it easier to load & run pre-trained models on mobile.
    landmarker_ops = landmarker_op (base_options=base_op(model_asset_path="hand_landmarker.task"), num_hands=1, running_mode=vis_mode) 
    model    = landmaker.create_from_options(landmarker_ops) # grabs a hand detection model
    image = Image.create_from_file(img)  # converts img to a format used by the above model
    data = model.detect(image)  # has a lot of stuff
    
    if len(data.hand_landmarks)==0: # gives array of 43 values ( (21,21) landmarks with(x,y) & 1 for hadn)
        return [0]*43 , data
    
    cords = [[p.x,p.y] for i in data.hand_landmarks for p in i]  # gives [[x1, y1], [x2, y2]...] we r not taking z axis
    cords = np.array(cords).reshape(-1)   # falttens 2d to 1d array

    hands = [x.category_name for y in data.handedness for x in y]   # which hand
    hands = [0 if a.lower()=="left" else 1 for a in hands]  # left hand = 0 , right = 1
    
    return hands + list(cords), data

In [48]:
# 4) converting coordinates and presense of hand to a dataframe

columns = ["gesture", "hand"] + [j+str(i) for i in range(21) for j in "xy"]
c=0
rows = []

for gesture in os.listdir("dataset/augmented/"):
    for img in os.listdir(f"dataset/augmented/{gesture}/"):
        coords, data = get_coords(f"dataset/augmented/{gesture}/{img}")

        if coords.count(0) > 15:
            continue  # skip over this cus img isnt recognised
        print([gesture] + coords)
        row = [gesture] + coords
        rows.append(row)
        c+=1

df = pd.DataFrame(rows, columns=columns)

['back', 1, 0.40835434198379517, 0.7980091571807861, 0.4686189889907837, 0.7880684733390808, 0.5203239917755127, 0.7340047359466553, 0.5671767592430115, 0.6776221990585327, 0.6134703159332275, 0.6312459707260132, 0.5237067937850952, 0.5369105935096741, 0.5784744620323181, 0.4231584668159485, 0.6146333813667297, 0.35030972957611084, 0.6433385014533997, 0.2894314229488373, 0.4943080544471741, 0.5129117965698242, 0.5423069596290588, 0.3778817057609558, 0.5798364877700806, 0.2880847752094269, 0.6109325289726257, 0.21753188967704773, 0.46045467257499695, 0.5129227638244629, 0.4891318678855896, 0.38297557830810547, 0.5129658579826355, 0.2932935655117035, 0.535499095916748, 0.22237586975097656, 0.4190661311149597, 0.535088062286377, 0.42282187938690186, 0.43131405115127563, 0.43103307485580444, 0.36312592029571533, 0.443550705909729, 0.30348294973373413]
['back', 1, 0.7380181550979614, 0.9539220929145813, 0.811631441116333, 0.9295036196708679, 0.8671398758888245, 0.8746638298034668, 0.9068105

In [49]:
df

gesture  hand        x0        y0        x1        y1        x2  \
0        back     1  0.408354  0.798009  0.468619  0.788068  0.520324   
1        back     1  0.738018  0.953922  0.811631  0.929504  0.867140   
2        back     1  0.778711  0.920021  0.829878  0.854544  0.839924   
3        back     1  0.544547  0.358544  0.594761  0.308408  0.615907   
4        back     1  0.639389  0.999641  0.705582  0.942861  0.724463   
...       ...   ...       ...       ...       ...       ...       ...   
10302      up     1  0.754574  0.482900  0.719018  0.410732  0.724717   
10303      up     1  0.400467  0.893043  0.324194  0.837651  0.300583   
10304      up     1  0.577286  0.981822  0.539540  0.921792  0.539803   
10305      up     1  0.059168  0.550714  0.026058  0.478095  0.037752   
10306      up     1  0.515002  0.702076  0.440132  0.645688  0.421084   

             y2        x3        y3  ...       x16       y16       x17  \
0      0.734005  0.567177  0.677622  ...  0.535499  0.222376  0.419066   
1      0.874664  0.906811  0.817538  ...  0.765333  0.504260  0.706651   
2      0.772804  0.838317  0.701273  ...  0.558117  0.488461  0.654203   
3      0.219479  0.625520  0.135604  ...  0.387815 -0.078149  0.427536   
4      0.867139  0.734841  0.798529  ...  0.484402  0.531440  0.545273   
...         ...       ...       ...  ...       ...       ...       ...   
10302  0.345831  0.752039  0.304875  ...  0.830973  0.203587  0.840634   
10303  0.765634  0.315447  0.711062  ...  0.375960  0.611945  0.439030   
10304  0.866299  0.564014  0.831321  ...  0.638205  0.750135  0.644468   
10305  0.415563  0.070713  0.381679  ...  0.150988  0.338609  0.172771   
10306  0.572473  0.440764  0.515162  ...  0.513286  0.454161  0.566358   

            y17       x18       y18       x19       y19       x20       y20  
0      0.535088  0.422822  0.431314  0.431033  0.363126  0.443551  0.303483  
1      0.751806  0.690427  0.681266  0.683598  0.633963  0.681377  0.591208  
2      0.748266  0.602408  0.690438  0.571133  0.646856  0.545295  0.606515  
3      0.147218  0.386324  0.078826  0.360226  0.033333  0.342553 -0.009822  
4      0.817315  0.499149  0.751139  0.474065  0.701526  0.454586  0.656380  
...         ...       ...       ...       ...       ...       ...       ...  
10302  0.333739  0.852603  0.285990  0.855865  0.261941  0.855788  0.245171  
10303  0.700523  0.429183  0.643411  0.423312  0.631999  0.417982  0.634353  
10304  0.865777  0.656714  0.826454  0.659757  0.807968  0.658912  0.794613  
10305  0.423598  0.189945  0.367816  0.181742  0.365005  0.173906  0.378077  
10306  0.502346  0.556794  0.445064  0.551906  0.454842  0.549003  0.476266  

[10307 rows x 44 columns]

In [50]:
df["hand"].sum()

9958

In [ ]:
# df.to_csv("co-ordinates1.csv",index=False)
# df

# 2) train model

In [5]:
# 1) importing modules
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.layers import InputLayer,Dropout,Dense
from tensorflow.nn import softmax
from tensorflow.keras.losses import SparseCategoricalCrossentropy
from tensorflow.keras.metrics import Accuracy, Precision, Recall

from sklearn.model_selection import train_test_split
from tensorflow.keras.callbacks import EarlyStopping

In [69]:
# 2) train test split
gestures = os.listdir("dataset/augmented")
dataset = pd.read_csv("co-ordinates1.csv")

print(gestures)
Y = pd.Series([gestures.index(g) for g in dataset["gesture"]])
X = dataset.drop(["gesture"],axis=1)

print(Y)
x_train, x_valid, y_train,  y_valid = train_test_split(X, Y, test_size=0.2, random_state=42)

['back', 'down', 'flip', 'front', 'left', 'right', 'up']
0        0
1        0
2        0
3        0
4        0
        ..
10302    6
10303    6
10304    6
10305    6
10306    6
Length: 10307, dtype: int64


In [70]:
# 3) model architecture

model = Sequential([
    InputLayer(input_shape=[43]),
    Dense(128,activation="relu",kernel_regularizer="l2"),
    Dense(64,activation="relu",kernel_regularizer="l2"),

    Dropout(0.2),

    Dense(64,activation="relu"),
    Dense(32,activation="relu"),
    Dense(8,activation="linear"),
])

model.summary()

c:\Users\Shivaay Dhondiyal\Desktop\shivaay\coding\2_development\projects\hand gestures\final\mediapipe_env\lib\site-packages\keras\src\layers\core\input_layer.py:27: UserWarning: Argument `input_shape` is deprecated. Use `shape` instead.
  warnings.warn(


Model: "sequential_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ dense_10 (Dense)                │ (None, 128)            │         5,632 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_11 (Dense)                │ (None, 64)             │         8,256 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 64)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_12 (Dense)                │ (None, 64)             │         4,160 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_13 (Dense)                │ (None, 32)             │         2,080 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_14 (Dense)                │ (None, 8)              │           264 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 20,392 (79.66 KB)

 Trainable params: 20,392 (79.66 KB)

 Non-trainable params: 0 (0.00 B)

In [71]:
# 4) training ur model

model.compile(loss=SparseCategoricalCrossentropy(from_logits=True),optimizer=Adam(1e-2),metrics=['accuracy'])
model.fit(x_train, y_train, epochs=100, validation_data=(x_valid,y_valid), callbacks=EarlyStopping(monitor='val_accuracy',patience=8,restore_best_weights=True))

Epoch 1/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 3s 5ms/step - accuracy: 0.2212 - loss: 2.0381 - val_accuracy: 0.3778 - val_loss: 1.3635
Epoch 2/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - accuracy: 0.3971 - loss: 1.3376 - val_accuracy: 0.4515 - val_loss: 1.2294
Epoch 3/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - accuracy: 0.4286 - loss: 1.3028 - val_accuracy: 0.4758 - val_loss: 1.1665
Epoch 4/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - accuracy: 0.4479 - loss: 1.2718 - val_accuracy: 0.4782 - val_loss: 1.1854
Epoch 5/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - accuracy: 0.4786 - loss: 1.1961 - val_accuracy: 0.4447 - val_loss: 1.3486
Epoch 6/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - accuracy: 0.5119 - loss: 1.1573 - val_accuracy: 0.5858 - val_loss: 0.9994
Epoch 7/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - accuracy: 0.5787 - loss: 1.0283 - val_accuracy: 0.6120 - val_loss: 0.9066
Epoch 8/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - accuracy: 0.5889 - loss: 1.0471 - val_accu

In [72]:
# 5) testing

pred1 = model.predict(x_valid) 
class_ = np.argmax(softmax(pred1), axis=1) # get class with highest probability for each test point
prob = np.max(softmax(pred1), axis=1)     # gives corresponding probabilities
comp = y_valid.to_numpy()     # actual class
# print(class_)
# print(prob)

a = Accuracy(name="accuracy")
a.update_state(class_, comp) # comapare the predicted & actual
a.result().numpy()

65/65 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step  


0.7594568

In [73]:
model.save("model1.keras")

# 3) hand gesture, voice recognition on drones

In [17]:
# 1) importing modules
import pybullet as p
import pybullet_data
from keras.models import load_model
from scipy.special import softmax

import speech_recognition as sr 
import whisper
import sounddevice as sd
import tempfile
import scipy.io.wavfile as wav

# import soundfile as sf
import wave
from pydub import AudioSegment
import re
whisper_model = whisper.load_model("medium") 

In [18]:
# 2) functions

def get_coords(img):
    base_op = tasks.BaseOptions 
    vis_mode = tasks.vision.RunningMode.IMAGE    
    landmaker = tasks.vision.HandLandmarker 
    landmarker_op = tasks.vision.HandLandmarkerOptions   
   
    landmarker_ops = landmarker_op (base_options=base_op(model_asset_path="hand_landmarker.task"), num_hands=1, running_mode=vis_mode) 
    model    = landmaker.create_from_options(landmarker_ops) 
    image = Image(image_format= ImageFormat.SRGB, data=img)  
    data = model.detect(image)  
    
    if len(data.hand_landmarks)==0: 
        return [0]*43 , data
    
    cords = [[p.x,p.y] for i in data.hand_landmarks for p in i]  
    cords = np.array(cords).reshape(-1)   

    hands = [x.category_name for y in data.handedness for x in y]  
    hands = [0 if a.lower()=="left" else 1 for a in hands]  
    
    return hands + list(cords), data

def draw_hand(img, raw):   # img with drawn landmarks is given as input
    points_on_hand = solutions.drawing_styles.get_default_hand_landmarks_style   # points on the hand (how they should look)
    connecting_lines = solutions.drawing_styles.get_default_hand_connections_style    # lines connecting the landmark (how they should look)

    for landmarks,hand_used in zip(raw.hand_landmarks, raw.handedness): # pairing set of landmarks with which hand is used
        proto_marks = landmark_pb2.NormalizedLandmarkList()       # stores points in a protobuf DS used by mp
        proto_marks.landmark.extend([landmark_pb2.NormalizedLandmark(x=L.x,y=L.y) for L in landmarks])    
        solutions.drawing_utils.draw_landmarks(img, proto_marks, solutions.hands.HAND_CONNECTIONS, points_on_hand(), connecting_lines())  
    return img


def voice_command():
    recogonizer = sr.Recognizer()    #  this obj is used to recognise speech from microphone
    with sr.Microphone() as src:     # this opens the microphone (with properly manages open & closing)
        print("listening for command")
        
        try: # to handel possible errors during the speech
            audio = recogonizer.listen(src, timeout=1)   # litens audio from the microphone for upto 2 secs
            command = recogonizer.recognize_google(audio)   # recognises speech using google API, stored as str in command
            print(f"command recognised: {command}")
            return command.lower()
        
        except sr.UnknownValueError:
            print("could not understand the command")
        except sr.RequestError:
            print("API unavailable")
        except sr.WaitTimeoutError:
            print("command undetected")

        return None
    

def voice_command():
    print("waiting....")
    duration = 5
    sample_rate = 16000
    filepath = "recorded_audio.wav"

    try:
        # get audio
        audio = sd.rec(int(duration * sample_rate), samplerate=sample_rate, channels=1, dtype='int16')
        sd.wait() 

        wav.write(filepath, sample_rate, audio)

        if not os.path.exists(filepath):
            print("Audio file not found after recording!")
            return None


        # use whisper
        result = whisper_model.transcribe(filepath, language="en")
        command = result["text"].strip().lower()
        
        command_words = [re.sub(r'[^a-z]', '', word) for word in command.split()]
        command_words = [word for word in command_words if word]

        if command:
            print(f"Command recognised: {command}")
            return command
        else:
            print("No command detected.")
            return None

    except Exception as e:
        print(f"Error: {str(e)}")
        return None

In [21]:
# 3) simulating drone with hand gesture

gesture_list = ['back', 'down', 'flip', 'front', 'left', 'right', 'up']

if p.isConnected():
    p.disconnect()

p.connect(p.GUI)  # connects pybullet to the user GUI
p.setAdditionalSearchPath(pybullet_data.getDataPath())  # Add PyBullet data such as path to URDF models like plane
p.loadURDF("plane.urdf")   # create the 2d infinite planne surface
model = load_model("model1.keras")
drone = p.loadURDF("r2d2.urdf", [0, 0, 0])

cap = cv2.VideoCapture(0)
if not cap.isOpened():
    print("Error: Could not open webcam.")
p.setGravity(0, 0, -9.8) 


main_frame = np.zeros(550 * 600 * 3, dtype=np.uint8).reshape(550, 600, 3)    # (height*width*no. of channels)
while True:
    
    flag , frame = cap.read()   # takes a frame
    frame = frame[0:480, 80:600, :]   # reduce unnessary processing and focus more on the hand gesture
    
    pts, raw = get_coords(cv2.cvtColor(frame, cv2.COLOR_BGR2RGB))   # get the coordinates of the hand from the frame, converts bgr(open cv) to rgb(compatible) format
    pickim = draw_hand(frame, raw)
    conf = 0

    # command = voice_command()
    
    if len(raw.handedness) != 0:  # checks for atleast 1 detected hand
        preds = model.predict(np.array(pts).reshape(1, 43), verbose=0) # supressing output logs and passing data in req format
        softout = softmax(preds)
        ans = gesture_list[np.argmax(softout)]  # gesture with highest confidence
        conf = np.max(softout)    # higehest confidence val coresponding to highest confidence
        
        print(ans, conf, list(softout.tolist()), list(pts), end="\r")
        print(f"Gesture: {ans}, Confidence: {conf}")

    
    main_frame[70:550, 80:600, :] = pickim   # updates a specific portion of the main frame using the img that we drew the hand

    # determines priority: voice or gesture
    if command in gesture_list:
        ans = command 
        conf = 1.0  
    
    if conf > 0.6:
        main_frame[:100, :350, :] = np.zeros(100 * 350 * 3).reshape(100, 350, 3)
        cv2.putText(main_frame, f"{ans}", [20, 20], 0, 0.5, color=[0, 255, 0])

        if "front" in ans:
            p.resetBaseVelocity(drone, linearVelocity=[0, 10, 0])
        elif "back" in ans:
            p.resetBaseVelocity(drone, linearVelocity=[0, -10, 0])
        elif "left" in ans:
            p.resetBaseVelocity(drone, linearVelocity=[-10, 0, 0])
        elif "right" in ans :
            p.resetBaseVelocity(drone, linearVelocity=[10, 0, 0])
        elif "up" in ans:
            p.resetBaseVelocity(drone, linearVelocity=[0, 0, 10])
        elif "down" in ans:
            p.resetBaseVelocity(drone, linearVelocity=[0, 0, -10])
        elif "flip" in ans:
            for _ in range(4): 
                # Apply angular velocity to rotate the drone around the x-axis
                p.resetBaseVelocity(drone, linearVelocity=[0, 0, 0], angularVelocity=[10, 0, 0]) 
                p.stepSimulation()
                time.sleep(1 / 240)  # Ensure consistent simulation timing
                # Reset angular velocity to stabilize the drone post-flip
            p.resetBaseVelocity(drone, angularVelocity=[0, 0, 0])


    else:
        main_frame[:70, :300, :] = np.zeros(70 * 300 * 3).reshape(70, 300, 3)
        p.resetBaseVelocity(drone, linearVelocity=[0, 0, 0], angularVelocity=[0, 0, 0]) # stop the bot
        cv2.putText(main_frame, f"no strong detection", [20, 20], 0, 0.5, color=[0, 0, 255])
    
    cv2.imshow("Frame", main_frame)
    
    if (cv2.waitKey(1) & 0xFF == ord('q')):
        break

    p.stepSimulation()
    time.sleep(1/240)  


cap.release()
cv2.destroyAllWindows()
p.disconnect()  # Disconnect from the simulation

Gesture: back, Confidence: 0.7532124519348145666770483832806, 0.00021002531866542995, 0.238521546125412, 0.0006116088479757309, 0.00663497019559145, 0.0006226827972568572, 4.6429828870486745e-09]] [1, 0.15389704704284668, 0.8965174555778503, 0.2539043724536896, 0.8853291869163513, 0.34221869707107544, 0.8357585668563843, 0.3842053711414337, 0.778433620929718, 0.35230183601379395, 0.7295118570327759, 0.2982213497161865, 0.6847586035728455, 0.33641791343688965, 0.585327684879303, 0.36805322766304016, 0.5479033589363098, 0.3989519476890564, 0.5306804776191711, 0.23505862057209015, 0.6654457449913025, 0.2541147768497467, 0.5489990711212158, 0.27882853150367737, 0.4944310188293457, 0.30420947074890137, 0.46109357476234436, 0.16802474856376648, 0.676670491695404, 0.16351263225078583, 0.5830485820770264, 0.16755074262619019, 0.5264037251472473, 0.17878025770187378, 0.48687806725502014, 0.10258205235004425, 0.7092949748039246, 0.07688429951667786, 0.6433468461036682, 0.0656953901052475, 0.5975

error: Not connected to physics server.